In [ ]:
from bokeh.models.ranges import Range1d
from PendingWriteRuntimeError import *

In [ ]:
class TestImageChannel(ImageChannel):
    
    def __init__(self, name):
        ImageChannel.__init__(self, name)
        self._current_index = 0
        self._iw, self._ih = 128, 128
        x, y = np.linspace(0, 10, self._iw), np.linspace(0, 10, self._ih)
        xx, yy = np.meshgrid(x, y)
        self._full_image = np.sin(xx) * np.cos(yy)
        self._inc = 1

    def __data(self):
        d = ChannelData(self.name)
        i = min(self._current_index, min(self._iw, self._ih))
        d.x_scale = (0, i)
        d.y_scale = (0, i)
        d.buffer = self._full_image[0:i+1, 0:i+1]
        self._current_index += self._inc
        if self._current_index > self._ih:
            self._current_index = self._ih
            self._inc *= -1 
        elif self._current_index < 0:
            self._current_index = 0
            self._inc *= -1
        return d
    
    def data(self): 
        return {self.name:self.__data()}

In [ ]:
import logging
logging.getLogger('tornado').setLevel(logging.ERROR)
logging.getLogger('bokeh.server').setLevel(logging.ERROR)

In [ ]:
ipa='127.0.0.1'

In [ ]:
dts = DataStream('dts', channels=[TestImageChannel('ic0')])
dsr = DataStreamer('dsr', data_streams=dts, update_period=0.1, ip_addr=ipa)
ctr = DataStreamerController(dsr)